(ch_ogr)=
# Vector data
Vector data are the second most common data type we work with in Geography - next to raster data, which we have covered already quite extensively during this course. The pages here have the goal to (a) give you an overview on the general structure of vector data, (b) make you familiar with some of the most common geospatial operations one does using vector data, and (c) provide code examples for these operations. As for the chapter on [raster data](ch_gdal), we avoid using external packages like ``shapely`` or ``geopandas``. This is, because we want you to understand the data structure of vector data and develop ideas on how to use them in a very efficient way. Likewise, the examples provided here are by no means exaustive, but provide you with the key elements to work in the context of this course. At the very bottom of this page, we provide some links to additional sources. The book by Garrard is provided in moodle. Yet, be aware that this is a bit outdated and sometimes not fully "to the point".

## The *OGR Simple Features Library*
In our geographic work, vector data are data in which geographic features are represented as discrete geometries:
* ``Points``: points represent the simplest type of gemetry. In geographical contexts they consist of two coordinates (e.g., latitude and longitude).
* ``Lines``: Lines are a collection of at least two points in a pre-defined order, where the first and the last point are not identical.
* ``Polygons``: Polygons are collections of at least three points in a pre-defined order, where the first and the last point are identical.

As you can see, all three types of vector data consist of individual points, stored as ``xy`` coordinates, so they are not fundamentally different in the way the carry spatial information. Compared to raster files, however, there are some distinct differences: (1) vector information only carry information **at the locations of the points**, and not between them (e.g., between two points that form a line. (2) For each geometry (or feature, as we will learn further below), we can store specific information (so-called *attributes*).

For our work here in the course, we will use the ``OGR Simple Features Library`` to work with the data - or simply: ``OGR``. It is a library that is part of [gdal](https://gdal.org/index.html), though, specifically focussing on working with **vector** formats. The most common formats you have probably worked with already, are *.shp*, *GeoJSON*, or *kml*. However, there are many more formats, some are more, some are less popular. Similar to [gdal](https://gdal.org/index.html), ``OGR`` gives as a set of tools and libaries on-hand for reading, writing, and manipulating geospatial vector data. In addition, we will employ the ``OGR Spatial Reference System (OSR)``, which is also a part of [gdal](https://gdal.org/index.html), but is focused on managing the spatial reference information of geospatial data. we will need this later on, when understanding and working with coordinate systems, projections, and datums used in voctor datasets.

Now let's have a look at the general data structure of a vector file:

```{figure} figures/flowchart.jpg
---
width: 100%
name: ogrOverview
---
Overview about the ``OGR`` vector structure. For more info and background visit the [ogr documentation](http://www.gdal.org/classGDALDataset.html#details) and see Garrard (2016) Geoprocessing in python chapters 3-5 (available in moodle).
```

Similar to the raster data structure, we can see the hierarchical nature of a vector layer. Take some time and look at the graph to understand the structure of a vector file. The structure is always the same, independently of the type of vector data (i.e., point, line, or polygon)

## Accessing vector data
Now that we know the structure, we can start loading some data. First, we will need to import the ``ogr`` and ``osr`` libraries and define our working folder:

In [6]:
import os
from osgeo import ogr, osr
folder = "D:/OneDrive - Conservation Biogeography Lab/_TEACHING/__Classes-Modules_HUB/M8_Geoprocessing-with-python/data/"

Now, we can open the shapefile. The shapefile that we are using here is a subset of the ``gadm`` dataset, which contains countries in form of polygons. As for raster data, the first levels of the file access (i.e., the file and the layer) create pointers to the actual data on the disc:

In [25]:
# Open the shapefile
ds = ogr.Open(folder + "EU_vector/gadm36.shp")
ds

<osgeo.ogr.DataSource; proxy of <Swig Object of type 'OGRDataSourceShadow *' at 0x000001CD02BDB210> >

In [26]:
# Get the first layer in the file
lyr = ds.GetLayer()
lyr

<osgeo.ogr.Layer; proxy of <Swig Object of type 'OGRLayerShadow *' at 0x000001CD0419E700> >

Ok, this was easy. But now let's see whether we can (a) get some general information about the shapefile, such as the projection, and (b) have a look at the different features and associated attributes within the layer:

In [27]:
# Spatial reference
sr = lyr.GetSpatialRef()
sr

<osgeo.osr.SpatialReference; proxy of <Swig Object of type 'OSRSpatialReferenceShadow *' at 0x000001CD04186010> >

As you can see, also the spatial reference is only a pointer to the actual information. If you want to store it as a variable and/or you want to read it, then you need to convert into something that the machine and store and work with. In the [raster chapter](ch_gdal) we introduced the function ``.ExportToWkt()``:

In [28]:
sr = lyr.GetSpatialRef().ExportToWkt()
sr

'GEOGCS["WGS 84",DATUM["WGS_1984",SPHEROID["WGS 84",6378137,298.257223563,AUTHORITY["EPSG","7030"]],AUTHORITY["EPSG","6326"]],PRIMEM["Greenwich",0,AUTHORITY["EPSG","8901"]],UNIT["degree",0.0174532925199433,AUTHORITY["EPSG","9122"]],AXIS["Latitude",NORTH],AXIS["Longitude",EAST],AUTHORITY["EPSG","4326"]]'

Now, that's better. Like in the [raster session](ch_gdal) we have the common lat/lon coordinate system (EPSG-code 4326). Below are some more code snippets, that allow you to get some additional information about the lyr:

In [29]:
# Get the name of the attributes
[field.name for field in lyr.schema]

['fid', 'iso_a2', 'NAME', 'FIPS_10_', 'ISO_A3', 'WB_A2', 'WB_A3']

In [30]:
# Get the total number of features in the lyr
lyr.GetFeatureCount()

9

## Accessing features
Knowing a layer's properties is nice, but really what we want to work with is the information of the individual features. We can access features in two main ways: (1) through indexing, and (b) by iterating over all elements (i.e., features inside) of a layer. We combine this here with a function that allows us to access an attribute of a feature (``.GetField()``)

First, let's access a single feature, and get the name from the attribute ``'NAME_0'``, which corresponds to the country name.

In [31]:
feat = lyr[5]
feat

<osgeo.ogr.Feature; proxy of <Swig Object of type 'OGRFeatureShadow *' at 0x000001CD04238AE0> >

In [33]:
ctr = feat.GetField('NAME')
ctr

'Switzerland'

Again, you can see that we access the feature through a pointer. However, getting the country name actually stores a value on the disc. Make sure to remember this when working with vector data.

Now, we rarely work with individual features, but instead we want to iterate over all features of a shapefile. We woould do this using a loop, and we got to know two different types of loops: the ``for``-loop and the ``while``-loop. Below we want to do the same as above, but now for all features of the shapefile. In case of the ``for``-loop, this is straight forward:

In [34]:
for feat in lyr:
    ctr = feat.GetField('NAME')
    print(ctr)

Germany
Netherlands
Austria
Liechtenstein
Belgium
Switzerland
Czechia
Luxembourg
Poland


In case of the ``while``-loop we need to employ another method associated with a layer: the ``.GetNextFeature()`` method. This methods works like a cursor inside a layer that always selects the next feature and works with it, until we want to access the next feature using the same method. Using ``.ResetReading()`` we can bring the cursor back to position 1:

In [36]:
feat = lyr.GetNextFeature()
while feat:
    ctr = feat.GetField('NAME')
    print(ctr)
    # Get the next feature
    feat = lyr.GetNextFeature()
# reset the reading
lyr.ResetReading()

Germany
Netherlands
Austria
Liechtenstein
Belgium
Switzerland
Czechia
Luxembourg
Poland


## Access geometries
The last part in terms of **accessing** the shapefile and its individual features is getting access to the geometry. As a recurring item, we have two options. (1) by creating a pointer to the geometry using the function ``.GetGeometryRef()`` and (2) by creating a copy of the geometry and copying it into memory. Both options have the application, as sometimes we don't want to manipulate a geometry (e.g., calculate an intersection) but only want to use the geometry to do some selections or calculations (e.g., calculate the area of a geometry). Before you continue, think of at least two other applications, where your choice would be to creating a pointer to a geometry or creating a copy of a geometry in memory.

In [39]:
# Ge the feature
feat = lyr[5]
# Version I: fetches the pointer to a feature geometry. Returned object is an OGRFeature.
geom_ref = feat.GetGeometryRef()
geom_ref

<osgeo.ogr.Geometry; proxy of <Swig Object of type 'OGRGeometryShadow *' at 0x000001CD041CA5E0> >

In [40]:
# Version II: Create a copy of the geometry in memory
geom_geom = feat.geometry()
geom_geom

<osgeo.ogr.Geometry; proxy of <Swig Object of type 'OGRGeometryShadow *' at 0x000001CD05383840> >

We see that in both cases we only get to see the address in the memory. if we want to get to know the coordinates that the geometry is composed of, we need to take a bit a detour and convert the geometry into a ``json`` element:

In [41]:
import json
ring_dict = json.loads(geom_geom.ExportToJson())
ring_dict

{'type': 'Polygon',
 'coordinates': [[[8.728973719134068, 46.10823576974391],
   [8.677485391750196, 46.09579213029839],
   [8.60183109429973, 46.122818895714566],
   [8.51026045756495, 46.207878327807165],
   [8.438120156269617, 46.23537014463381],
   [8.42323734385719, 46.27583280294639],
   [8.441634152733435, 46.43494451653792],
   [8.385906922465184, 46.450205969091265],
   [8.316267126318513, 46.43365257734048],
   [8.28660486070453, 46.40535983631927],
   [8.29146244339154, 46.378358873652715],
   [8.192553751627255, 46.309164116610646],
   [8.087340534124792, 46.27180204540798],
   [8.073077841154136, 46.253611982247826],
   [8.129508502830177, 46.19604438956186],
   [8.132299032786491, 46.15935416276402],
   [8.110594931346299, 46.1269530500795],
   [8.025328817655055, 46.091141269326485],
   [7.985848021160997, 45.999312218804654],
   [7.898204793952982, 45.98194895302413],
   [7.870201293240803, 45.940369641378744],
   [7.84962011447879, 45.93971203023916],
   [7.83123213609

Using these tools you are ready to access shapefiles, get some basic information about the layer, iterate over the individual features and access the attributes and geometries. In the next chapters, we will pay more attention to some more geographic applications. For some further reading, have a look at:
1. Garrard: Geoprocessing in python, chapters 3-5
2. Summary of some [main methods using the ogr libraries](https://pcjericks.github.io/py-gdalogr-cookbook/). Some of the materials provided here are inspired by this website.